In [1]:
import pandas as pd
import json
import folium
from geojson import FeatureCollection
import geopandas as gpd
from pandas.io.json import json_normalize
%matplotlib inline


Bad key "text.kerning_factor" on line 4 in
/Users/jbramall/opt/anaconda3/lib/python3.7/site-packages/matplotlib/mpl-data/stylelib/_classic_test_patch.mplstyle.
You probably need to get an updated matplotlibrc file from
https://github.com/matplotlib/matplotlib/blob/v3.1.3/matplotlibrc.template
or from the matplotlib source distribution


#### flatten the json data to get id table

In [2]:
with open('_data/uk_la.geojson') as json_file:
    data = json.load(json_file)

In [3]:
data_normalized = json_normalize(data['features'], max_level=None)

/Users/jbramall/opt/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:1: FutureWarning: pandas.io.json.json_normalize is deprecated, use pandas.json_normalize instead
  """Entry point for launching an IPython kernel.


In [4]:
#each id in the geoJSON has a corresponding area name - this is what we use to join to the google data
map_values = data_normalized[['id','properties.name']]
map_values.head(2)

id    properties.name
0   0  Rhondda Cynon Taf
1   1        Eilean Siar

#### join the google data

In [5]:
#join on semantic region name: nb these do not tally up perfectly between datasets
#the matching between names is done manually in the geomappings.csv file
df = pd.read_csv('_data/Global_Mobility_Report.csv')
mappings = pd.read_csv('_data/geomappings.csv')
mappings = mappings.dropna(subset=['google_region_names'])

/Users/jbramall/opt/anaconda3/lib/python3.7/site-packages/IPython/core/interactiveshell.py:3063: DtypeWarning: Columns (3) have mixed types.Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)


In [6]:
#apply a date filter before merging to get latest data
df['date'] = pd.to_datetime(df['date'])
latest_date = df['date'].max()
df = df.loc[df['date'] == latest_date]

In [7]:
data_cols = df.filter(regex="_percent_change_from_baseline").columns.to_list()
data_cols.append('sub_region_1')
data_cols

['retail_and_recreation_percent_change_from_baseline',
 'grocery_and_pharmacy_percent_change_from_baseline',
 'parks_percent_change_from_baseline',
 'transit_stations_percent_change_from_baseline',
 'workplaces_percent_change_from_baseline',
 'residential_percent_change_from_baseline',
 'sub_region_1']

In [8]:
df_m = pd.merge(mappings,df[data_cols],left_on='google_region_names',right_on='sub_region_1',how='left')

In [9]:
#group the google data by geoJSON region to get mean of all the movement indices for each geoJSON region
region_values = df_m.groupby('geoJSON_region').mean()
region_values = region_values.mean(axis=1)
region_values.name = 'mean_percent_change_from_baseline'

In [10]:
folium_values = pd.merge(map_values,region_values,left_on='properties.name',right_index=True)

In [11]:
#filter the json
folium_data = [i for i in data['features'] if i['properties']['name'] in folium_values['properties.name'].to_list()]
folium_data = FeatureCollection(folium_data)

In [12]:
m = folium.Map(location=[51.5, -0.11], zoom_start=10, tiles='cartodbpositron')
folium.Choropleth(geo_data=folium_data,
                  data=folium_values,
                  columns=['id','mean_percent_change_from_baseline'],
                  key_on='feature.id',
                  fill_color='OrRd',
                  legend_name='Legend Title',
                 ).add_to(m)
m